### Querying the BEA API

In [1]:
import requests
from pprint import pprint
from config import api_key
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import csv
import os

In [2]:
url = "https://apps.bea.gov/api/data?"

### Build query URL

### Personal income from 2013-2017 for all counties, in JSON format 

In [3]:
income_query_url = url + "UserID=" + api_key + "&method=GetData&Datasetname=RegionalIncome&TableName=CA1&LineCode=1&GeoFips=COUNTY&ResultFormat=JSON"
income_data = requests.get(income_query_url).json()
pprint(income_data)

{'BEAAPI': {'Request': {'RequestParam': [{'ParameterName': 'USERID',
                                          'ParameterValue': '29E04437-F92A-4CAE-9F6E-5E49B1790A37'},
                                         {'ParameterName': 'METHOD',
                                          'ParameterValue': 'GETDATA'},
                                         {'ParameterName': 'LINECODE',
                                          'ParameterValue': '1'},
                                         {'ParameterName': 'DATASETNAME',
                                          'ParameterValue': 'REGIONALINCOME'},
                                         {'ParameterName': 'RESULTFORMAT',
                                          'ParameterValue': 'JSON'},
                                         {'ParameterName': 'TABLENAME',
                                          'ParameterValue': 'CA1'},
                                         {'ParameterName': 'GEOFIPS',
                                          'Pa

In [4]:
income=income_data["BEAAPI"]["Results"]["Data"]

In [5]:
income[0]

{'Code': 'CA1-1',
 'GeoFips': '00000',
 'GeoName': 'United States',
 'TimePeriod': '2013',
 'CL_UNIT': 'Thousands of dollars',
 'UNIT_MULT': '3',
 'DataValue': '14,175,503,000'}

### Loop through each result and append results into lists

In [6]:
county_id=[]
geo=[]
Year=[]
Unit=[]
Income=[]
for i in range(len(income)):
    county_id.append(income[i]["GeoFips"])
    geo.append(income[i]["GeoName"])
    Year.append(income[i]["TimePeriod"])
    Unit.append(income[i]["CL_UNIT"])
    Income.append(income[i]["DataValue"])

### Create Dataframe from the column above

In [7]:
income_df = pd.DataFrame({
    "County_id": county_id,
    "Geo": geo,
    "Year":Year,
    "Unit":Unit,
    "Income":Income
})



### Split the Geo column into two separate columns with county and state information

In [8]:
income_df[['county_name','state_code']] = income_df['Geo'].str.split(',',n=1, expand=True)


In [14]:
clean_income_df=income_df.drop(columns=['Geo'])
clean_income_df

County_id  Year                  Unit          Income     county_name  \
0         00000  2013  Thousands of dollars  14,175,503,000   United States   
1         00000  2014  Thousands of dollars  14,983,140,000   United States   
2         00000  2015  Thousands of dollars  15,711,634,000   United States   
3         00000  2016  Thousands of dollars  16,115,630,000   United States   
4         00000  2017  Thousands of dollars  16,820,250,000   United States   
5         01000  2013  Thousands of dollars     174,118,716         Alabama   
6         01000  2014  Thousands of dollars     180,220,290         Alabama   
7         01000  2015  Thousands of dollars     187,301,605         Alabama   
8         01000  2016  Thousands of dollars     190,991,192         Alabama   
9         01000  2017  Thousands of dollars     198,916,425         Alabama   
10        01001  2013  Thousands of dollars       1,939,719         Autauga   
11        01001  2014  Thousands of dollars       2,012,244         Autauga   
12        01001  2015  Thousands of dollars       2,116,276         Autauga   
13        01001  2016  Thousands of dollars       2,183,987         Autauga   
14        01001  2017  Thousands of dollars       2,247,046         Autauga   
15        01003  2013  Thousands of dollars       7,441,318         Baldwin   
16        01003  2014  Thousands of dollars       7,875,234         Baldwin   
17        01003  2015  Thousands of dollars       8,400,864         Baldwin   
18        01003  2016  Thousands of dollars       8,923,673         Baldwin   
19        01003  2017  Thousands of dollars       9,372,465         Baldwin   
20        01005  2013  Thousands of dollars         809,476         Barbour   
21        01005  2014  Thousands of dollars         800,883         Barbour   
22        01005  2015  Thousands of dollars         827,557         Barbour   
23        01005  2016  Thousands of dollars         818,333         Barbour   
24        01005  2017  Thousands of dollars         845,349         Barbour   
25        01007  2013  Thousands of dollars         617,036            Bibb   
26        01007  2014  Thousands of dollars         636,539            Bibb   
27        01007  2015  Thousands of dollars         655,342            Bibb   
28        01007  2016  Thousands of dollars         656,112            Bibb   
29        01007  2017  Thousands of dollars         680,543            Bibb   
...         ...   ...                   ...             ...             ...   
15960     93000  2013  Thousands of dollars   1,980,331,726     Great Lakes   
15961     93000  2014  Thousands of dollars   2,069,388,977     Great Lakes   
15962     93000  2015  Thousands of dollars   2,159,301,238     Great Lakes   
15963     93000  2016  Thousands of dollars   2,206,069,166     Great Lakes   
15964     93000  2017  Thousands of dollars   2,283,656,418     Great Lakes   
15965     94000  2013  Thousands of dollars     931,393,230          Plains   
15966     94000  2014  Thousands of dollars     971,529,497          Plains   
15967     94000  2015  Thousands of dollars   1,003,740,008          Plains   
15968     94000  2016  Thousands of dollars   1,016,404,570          Plains   
15969     94000  2017  Thousands of dollars   1,047,114,527          Plains   
15970     95000  2013  Thousands of dollars   3,164,660,287       Southeast   
15971     95000  2014  Thousands of dollars   3,350,202,976       Southeast   
15972     95000  2015  Thousands of dollars   3,526,432,903       Southeast   
15973     95000  2016  Thousands of dollars   3,626,161,085       Southeast   
15974     95000  2017  Thousands of dollars   3,783,717,362       Southeast   
15975     96000  2013  Thousands of dollars   1,642,200,054       Southwest   
15976     96000  2014  Thousands of dollars   1,762,040,572       Southwest   
15977     96000  2015  Thousands of dollars   1,805,775,989       Southwest   
15978     96000  2016  Thousands of dollars   1,814,966,

In [15]:
# Remove the ',' from the string
clean_income_df.Income=clean_income_df.Income.apply(lambda x :x.replace(",",""))
clean_income_df

County_id  Year                  Unit       Income     county_name  \
0         00000  2013  Thousands of dollars  14175503000   United States   
1         00000  2014  Thousands of dollars  14983140000   United States   
2         00000  2015  Thousands of dollars  15711634000   United States   
3         00000  2016  Thousands of dollars  16115630000   United States   
4         00000  2017  Thousands of dollars  16820250000   United States   
5         01000  2013  Thousands of dollars    174118716         Alabama   
6         01000  2014  Thousands of dollars    180220290         Alabama   
7         01000  2015  Thousands of dollars    187301605         Alabama   
8         01000  2016  Thousands of dollars    190991192         Alabama   
9         01000  2017  Thousands of dollars    198916425         Alabama   
10        01001  2013  Thousands of dollars      1939719         Autauga   
11        01001  2014  Thousands of dollars      2012244         Autauga   
12        01001  2015  Thousands of dollars      2116276         Autauga   
13        01001  2016  Thousands of dollars      2183987         Autauga   
14        01001  2017  Thousands of dollars      2247046         Autauga   
15        01003  2013  Thousands of dollars      7441318         Baldwin   
16        01003  2014  Thousands of dollars      7875234         Baldwin   
17        01003  2015  Thousands of dollars      8400864         Baldwin   
18        01003  2016  Thousands of dollars      8923673         Baldwin   
19        01003  2017  Thousands of dollars      9372465         Baldwin   
20        01005  2013  Thousands of dollars       809476         Barbour   
21        01005  2014  Thousands of dollars       800883         Barbour   
22        01005  2015  Thousands of dollars       827557         Barbour   
23        01005  2016  Thousands of dollars       818333         Barbour   
24        01005  2017  Thousands of dollars       845349         Barbour   
25        01007  2013  Thousands of dollars       617036            Bibb   
26        01007  2014  Thousands of dollars       636539            Bibb   
27        01007  2015  Thousands of dollars       655342            Bibb   
28        01007  2016  Thousands of dollars       656112            Bibb   
29        01007  2017  Thousands of dollars       680543            Bibb   
...         ...   ...                   ...          ...             ...   
15960     93000  2013  Thousands of dollars   1980331726     Great Lakes   
15961     93000  2014  Thousands of dollars   2069388977     Great Lakes   
15962     93000  2015  Thousands of dollars   2159301238     Great Lakes   
15963     93000  2016  Thousands of dollars   2206069166     Great Lakes   
15964     93000  2017  Thousands of dollars   2283656418     Great Lakes   
15965     94000  2013  Thousands of dollars    931393230          Plains   
15966     94000  2014  Thousands of dollars    971529497          Plains   
15967     94000  2015  Thousands of dollars   1003740008          Plains   
15968     94000  2016  Thousands of dollars   1016404570          Plains   
15969     94000  2017  Thousands of dollars   1047114527          Plains   
15970     95000  2013  Thousands of dollars   3164660287       Southeast   
15971     95000  2014  Thousands of dollars   3350202976       Southeast   
15972     95000  2015  Thousands of dollars   3526432903       Southeast   
15973     95000  2016  Thousands of dollars   3626161085       Southeast   
15974     95000  2017  Thousands of dollars   3783717362       Southeast   
15975     96000  2013  Thousands of dollars   1642200054       Southwest   
15976     96000  2014  Thousands of dollars   1762040572       Southwest   
15977     96000  2015  Thousands of dollars   1805775989       Southwest   
15978     96000  2016  Thousands of dollars   1814966983       Southwest   
15979     96000  2017  Thousands of dollars   1894779972       Southwest   
15980     97000  2013  Thousands of dollars    4853858

In [18]:
# Convert the string to numeric number
clean_income_df['Income'] = pd.to_numeric(clean_income_df['Income'],errors='coerce')
clean_income_df.head()

County_id  Year                  Unit        Income    county_name  \
0     00000  2013  Thousands of dollars  1.417550e+10  United States   
1     00000  2014  Thousands of dollars  1.498314e+10  United States   
2     00000  2015  Thousands of dollars  1.571163e+10  United States   
3     00000  2016  Thousands of dollars  1.611563e+10  United States   
4     00000  2017  Thousands of dollars  1.682025e+10  United States   

  state_code  
0       None  
1       None  
2       None  
3       None  
4       None

### Calculate the average personal income from 2013 to 2017

In [19]:
grouped_county_df = clean_income_df.groupby(['state_code','county_name'])

In [20]:
income_county_total = grouped_county_df["Income"].mean()
income_county_total

state_code  county_name                 
 AK         Anchorage Municipality          18327394.0
            Bristol Bay Borough               106655.6
            Fairbanks North Star Borough     5233550.6
            Haines Borough                    139632.2
            Juneau City and Borough          2061304.8
            Kenai Peninsula Borough          2850601.2
            Kodiak Island Borough             801196.0
            Matanuska-Susitna Borough        4551680.4
            North Slope Borough               893510.8
            Northwest Arctic Borough          334842.6
            Sitka City and Borough            571257.6
 AK*        Aleutian Islands Census Area           NaN
            Aleutian Islands Division              NaN
            Aleutians East Borough            165461.2
            Aleutians West Census Area        304076.2
            Angoon Division                        NaN
            Barrow-North Slope Division            NaN
            Bethel Censu

### Save the average income into a new dataframe

In [26]:

average_income = pd.DataFrame({"Income":income_county_total})
average_income

Income
state_code county_name                             
 AK        Anchorage Municipality        18327394.0
           Bristol Bay Borough             106655.6
           Fairbanks North Star Borough   5233550.6
           Haines Borough                  139632.2
           Juneau City and Borough        2061304.8
           Kenai Peninsula Borough        2850601.2
           Kodiak Island Borough           801196.0
           Matanuska-Susitna Borough      4551680.4
           North Slope Borough             893510.8
           Northwest Arctic Borough        334842.6
           Sitka City and Borough          571257.6
 AK*       Aleutian Islands Census Area         NaN
           Aleutian Islands Division            NaN
           Aleutians East Borough          165461.2
           Aleutians West Census Area      304076.2
           Angoon Division                      NaN
           Barrow-North Slope Division          NaN
           Bethel Census Area              728503.2
           Bethel Division                      NaN
           Bristol Bay Division                 NaN
           Cordova-McCarthy Division            NaN
           Denali Borough                  151897.0
           Dillingham Census Area          271694.8
           Haines Division                      NaN
           Hoonah-Angoon Census Area       115080.2
           Kenai-Cook Inlet Division            NaN
           Ketchikan Gateway Borough       869082.0
           Kusilvak Census Area            239077.8
           Kuskokwim Division                   NaN
           Lake and Peninsula Borough       89582.2
...                                             ...
 WV        Upshur                          760893.6
           Wayne                          1209734.8
           Webster                         227184.4
           Wetzel                          486946.2
           Wirt                            169300.6
           Wood                           3270180.4
           Wyoming                         621027.4
 WY        Albany                         1498412.4
           Big Horn                        431413.4
           Campbell                       2487030.4
           Carbon                          797393.4
           Converse                        703652.0
           Crook                           334900.8
           Fremont                        1691507.8
           Goshen                          545835.2
           Hot Springs                     236294.0
           Johnson                         421710.6
           Laramie                        4790444.8
           Lincoln                         720701.2
           Natrona                        5482005.0
           Niobrara                        108742.6
           Park                           1452494.6
           Platte                          397933.4
           Sheridan                       1576712.8
           Sublette                        508717.4
           Sweetwater                     2167303.2
           Teton                          4780344.8
           Uinta                           804935.2
           Washakie                        362701.6
           Weston                          319290.2

[3138 rows x 1 columns]

### Export the income resutls into csv file

In [46]:
average_income.to_csv('average_income.csv')
clean_income_df.to_csv('income_2013to2017.csv')

### Real per capita personal income for all states, all years (2008-2016), in JSON format 

In [29]:
capi_url = url + "UserID=" + api_key + "&method=GetData&Datasetname=RegionalIncome&TableName=RPI1&lineCode=2&Year=ALL&GeoFips=STATE&ResultFormat=JSON"
capi_data = requests.get(capi_url).json()
pprint(capi_data)

{'BEAAPI': {'Request': {'RequestParam': [{'ParameterName': 'YEAR',
                                          'ParameterValue': 'ALL'},
                                         {'ParameterName': 'METHOD',
                                          'ParameterValue': 'GETDATA'},
                                         {'ParameterName': 'TABLENAME',
                                          'ParameterValue': 'RPI1'},
                                         {'ParameterName': 'GEOFIPS',
                                          'ParameterValue': 'STATE'},
                                         {'ParameterName': 'USERID',
                                          'ParameterValue': '29E04437-F92A-4CAE-9F6E-5E49B1790A37'},
                                         {'ParameterName': 'LINECODE',
                                          'ParameterValue': '2'},
                                         {'ParameterName': 'DATASETNAME',
                                          'ParameterValue': 'R

In [30]:
capi_income = capi_data["BEAAPI"]["Results"]["Data"]
capi_income[1]

{'Code': 'RPI1-2',
 'GeoFips': '00000',
 'GeoName': 'United States',
 'TimePeriod': '2009',
 'CL_UNIT': 'Chained 2012 dollars',
 'UNIT_MULT': '0',
 'DataValue': '41,750'}

In [31]:
county_id=[]
geo=[]
Year=[]
Income=[]
for i in range(len(capi_income)):
    county_id.append(capi_income[i]["GeoFips"])
    geo.append(capi_income[i]["GeoName"])
    Year.append(capi_income[i]["TimePeriod"])
    Income.append(capi_income[i]["DataValue"])

In [34]:
percapita_income_df = pd.DataFrame({
    "County_id": county_id,
    "State_name": geo,
    "Year":Year,
    "Income":Income
})


In [50]:
percapita_income_df

County_id     State_name  Year  Income
0       00000  United States  2008   43431
1       00000  United States  2009   41750
2       00000  United States  2010   42364
3       00000  United States  2011   43541
4       00000  United States  2012   44582
5       00000  United States  2013   44230
6       00000  United States  2014   45713
7       00000  United States  2015   47456
8       00000  United States  2016   47807
9       01000        Alabama  2008   40551
10      01000        Alabama  2009   39763
11      01000        Alabama  2010   40310
12      01000        Alabama  2011   40717
13      01000        Alabama  2012   40745
14      01000        Alabama  2013   40626
15      01000        Alabama  2014   41648
16      01000        Alabama  2015   43272
17      01000        Alabama  2016   43684
18      02000         Alaska  2008   47393
19      02000         Alaska  2009   46732
20      02000         Alaska  2010   48898
21      02000         Alaska  2011   50571
22      02000         Alaska  2012   50498
23      02000         Alaska  2013   49232
24      02000         Alaska  2014   50882
25      02000         Alaska  2015   52712
26      02000         Alaska  2016   51079
27      04000        Arizona  2008   37615
28      04000        Arizona  2009   35486
29      04000        Arizona  2010   35651
..        ...            ...   ...     ...
438     53000     Washington  2014   47793
439     53000     Washington  2015   49776
440     53000     Washington  2016   50640
441     54000  West Virginia  2008   38332
442     54000  West Virginia  2009   38329
443     54000  West Virginia  2010   38371
444     54000  West Virginia  2011   39465
445     54000  West Virginia  2012   39770
446     54000  West Virginia  2013   39036
447     54000  West Virginia  2014   39844
448     54000  West Virginia  2015   40343
449     54000  West Virginia  2016   40619
450     55000      Wisconsin  2008   44567
451     55000      Wisconsin  2009   43712
452     55000      Wisconsin  2010   44004
453     55000      Wisconsin  2011   45026
454     55000      Wisconsin  2012   45999
455     55000      Wisconsin  2013   45674
456     55000      Wisconsin  2014   46723
457     55000      Wisconsin  2015   48567
458     55000      Wisconsin  2016   49211
459     56000        Wyoming  2008   53408
460     56000        Wyoming  2009   48251
461     56000        Wyoming  2010   50252
462     56000        Wyoming  2011   52911
463     56000        Wyoming  2012   56159
464     56000        Wyoming  2013   54651
465     56000        Wyoming  2014   56940
466     56000        Wyoming  2015   57629
467     56000        Wyoming  2016   55183

[468 rows x 4 columns]

In [41]:
### convert the string to numeric number (income column)
percapita_income_df.Income=percapita_income_df.Income.apply(lambda x :x.replace(",",""))
percapita_income_df['Income'] = pd.to_numeric(percapita_income_df['Income'],errors='coerce')

In [45]:
percapita_income_df.head()

County_id     State_name  Year  Income
0     00000  United States  2008   43431
1     00000  United States  2009   41750
2     00000  United States  2010   42364
3     00000  United States  2011   43541
4     00000  United States  2012   44582

In [47]:
percapita_income_df.to_csv('percapita_income_2008to2016.csv')

### Scrape the FIPS code table information for county and state from website 

In [48]:
url = 'https://www.nrcs.usda.gov/wps/portal/nrcs/detail/national/home/?cid=nrcs143_013697'

In [52]:
tables = pd.read_html(url)
tables[0]

FIPS           Name State
0                                                 01001        Autauga    AL
1                                                 01003        Baldwin    AL
2                                                 01005        Barbour    AL
3                                                 01007           Bibb    AL
4                                                 01009         Blount    AL
5                                                 01011        Bullock    AL
6                                                 01013         Butler    AL
7                                                 01015        Calhoun    AL
8                                                 01017       Chambers    AL
9                                                 01019       Cherokee    AL
10                                                01021        Chilton    AL
11                                                01023        Choctaw    AL
12                                                01025         Clarke    AL
13                                                01027           Clay    AL
14                                                01029       Cleburne    AL
15                                                01031         Coffee    AL
16                                                01033        Colbert    AL
17                                                01035        Conecuh    AL
18                                                01037          Coosa    AL
19                                                01039      Covington    AL
20                                                01041       Crenshaw    AL
21                                                01043        Cullman    AL
22                                                01045           Dale    AL
23                                                01047         Dallas    AL
24                                                01049        De Kalb    AL
25                                                01051         Elmore    AL
26                                                01053       Escambia    AL
27                                                01055         Etowah    AL
28                                                01057        Fayette    AL
29                                                01059       Franklin    AL
...                                                 ...            ...   ...
3203                                              72103        Nabuabo    PR
3204                                              72105      Naranjito    PR
3205                                              72107       Orocovis    PR
3206                                              72109       Patillas    PR
3207                                              72111       Penuelas    PR
3208                                              72113          Ponce    PR
3209                                              72115   Quebradillas    PR
3210                                              72117         Rincon    PR
3211                                              72119     Rio Grande    PR
3212                                              72121  Sabana Grande    PR
3213                                              72123        Salinas    PR
3214                                              72125     San German    PR
3215                                              72127       San Juan    PR
3216                                              72129    San Lorenzo    PR
3217                                              72131  San Sabastian    PR
3218                                              72133   Santa Isabel    PR
3219                                              72135       Toa Alta    PR
3220                                              72137       Toa Baja    PR
3221                                              72139  Trujillo Alto    PR
3222                                              72141         Utuado    PR
3223                                           

In [53]:
tables[0].to_csv('states_FIPs.csv')

### Drinking water violation records from USEPA

In [55]:
# Make a reference to the water_system.csv file path
csv_path = os.path.join( "water_system_geographic_area.csv")
# Import the water_system.csv file as a DataFrame
water_system_df = pd.read_csv(csv_path,encoding="ISO-8859-1")
water_system_df

PWS ID                                PWS Name  EPA Region  \
0       NJ1710003               PICNIC GROVE MOBILE HOMES           2   
1       LA1063022             TOWN OF ALBANY WATER SYSTEM           6   
2       NY0140001                            NEW SALEM WD           2   
3       MN1230013                                  Wykoff           5   
4       WY5601596   BENNOR ESTATES & IMPROVEMENT DISTRICT           8   
5       OK3003801                                  GOTEBO           6   
6       OK2000811                           GRACEMONT PWA           6   
7       OK3000606                          GREENFIELD PWA           6   
8       OK2004223                            RODEO CORNER           6   
9       OK2004255                  LAZY E TRAINING CENTER           6   
10      OK2004250                            LAZY E ARENA           6   
11      MO5031104                 BRIAR CLIFF SUBDIVISION           7   
12      OK2004247   CENTRAL OKLAHOMA CAMP AND CONF CENTER           6   
13      OK2004207                         LOGAN CO RWD #1           6   
14      OK1020903                                 GUTHRIE           6   
15      MN1230014                        Rushford Village           5   
16      MN1240001                              Albert Lea           5   
17      OK2005506                                  HARRAH           6   
18      OK4002610                             COUNTRY MHP           6   
19      MO4212840                        MATTS STEAKHOUSE           7   
20      WA5388785                     TOOP WATER ASSN INC          10   
21      WA5329450               GREEN MEADOWS SUBDIVISION          10   
22      OR4101209                   SAUVIE ISLAND MOORAGE          10   
23      MO5182849                      JM & M INVESTMENTS           7   
24      WA5331362                 HARMONY PARK LOT OWNERS          10   
25      WA53AB022                     OLERIN WATER SYSTEM          10   
26      WA5329440                       Green Lantern Pub          10   
27      WA5303774               MOUNTAIN VIEW SUBDIVISION          10   
28      WA5341140          MOUNT ADAMS VISTA WATER SYSTEM          10   
29      CT0960091     CANDLEWOOD TRAILS ASSOCIATION, INC.           1   
...           ...                                     ...         ...   
146168  VT0004318                 BEST WESTERN BENNINGTON           1   
146169  WA5306372                         Annas Mini Mart          10   
146170  WA5306390                  ECHO VALLEY SKI RESORT          10   
146171  WA5306514        SUNSET WATER & MAINTENANCE ASSOC          10   
146172  WA5306519                      WOODBRIDGE GARDENS          10   
146173  WA5306556                           SANDHILL PARK          10   
146174  WA5306618                              METAL MILL          10   
146175  NY1830042                           OAKFIELD TOWN           2   
146176  CA3705067                         MOM S PIE HOUSE           9   
146177  CA4100537                 SILVA WHOLESALE FLORIST           9   
146178  CA4100600                     LA HONDA PROPERTIES           9   
146179  CA1300611            SHUEY SHELL CANYON WATER CO.           9   
146180  WA5375670                 SAMISH RIVER PARK, INC.          10   
146181  WA5382200               SOUTH OTHELLO WATER USERS          10   
146182  MA3330027  PURA VIDA @ NEW ENGLAN SPORTS ACCADEMY           1   
146183  MA1341029                SWEET BROOK NURSING HOME           1   
146184  CA3303007                    IRENE RODRIGUEZ CAMP           9   
146185  CA3701893                         DUDLEY'S BAKERY           9   
146186  CA5000378              TONY MORRIS / MORRIS DAIRY           9   
146187  CA5000247                    CERVANTES LABOR CAMP           9   
146188  CA5304101                Hawkins Bar Trailer Park           9   
146189  CA3500551              Live Oak Water Association           9   
146190  MD1061068           NEW YORK J&P PIZZA ELDERSBURG           3

In [56]:

water_system_df.rename(columns={"County Served":"county_name","Primacy Agency":"State_name"}, inplace=True)

In [58]:
water_system_df.head()

PWS ID                               PWS Name  EPA Region  State_name  \
0  NJ1710003              PICNIC GROVE MOBILE HOMES           2  New Jersey   
1  LA1063022            TOWN OF ALBANY WATER SYSTEM           6   Louisiana   
2  NY0140001                           NEW SALEM WD           2    New York   
3  MN1230013                                 Wykoff           5   Minnesota   
4  WY5601596  BENNOR ESTATES & IMPROVEMENT DISTRICT           8     Wyoming   

                 PWS Type Primacy Type Area Type        county_name  \
0  Community water system        State    County              Salem   
1  Community water system        State    County  Livingston Parish   
2  Community water system        State    County             Albany   
3  Community water system        State    County           Fillmore   
4  Community water system        State    County           Campbell   

  City Served Zip Code Served Activity Status Deactivation Date  \
0           -               -          Active                 -   
1           -               -          Active                 -   
2           -               -          Active                 -   
3           -               -          Active                 -   
4           -               -          Active                 -   

  Is Source Water Protected  Population Served Count State Code Zip Code  
0                         N                      250         NJ    08328  
1                         N                     6063         LA    70711  
2                         -                      350         NY    12159  
3                         -                      444         MN    55990  
4                         N                      174         WY    82717

In [59]:
water_system_df.to_csv('water_system.csv')